In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import sys
project_path = '/Users/daniela/Documents/swan/swan_model_builder_tool'
sys.path.append(project_path)


In [4]:
import load_config as lc

run_name = 'peninsula_paracas'  # Hardcoded run name
config_path = f'{project_path}/experiments_specs.txt'
config = lc.load_run_config(config_path, run_name)


In [5]:

def create_main_directories(config):
    import os
    base_path = config['base']['path']
    output_dir = base_path + config['output']['directory']

    for folder in config['output']['data'].values():
        dir = f'{output_dir}/{folder}'
        if not os.path.isdir(dir):
            print(f'Creating file {dir}')
            os.makedirs(dir, exist_ok=True)
        else:
            print(f'{dir} already exists')
    
    for folder in config['output']['subdirectories']:
        dir = f'{output_dir}/{folder}'
        if not os.path.isdir(dir):
            print(f'Creating file {dir}')
            os.makedirs(dir, exist_ok=True)
        else:
            print(f'{dir} already exists')

In [6]:
create_main_directories(config)

/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/DATA/WIND already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/DATA/WAVE already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/DATA/BATHY already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/QGIS already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/SWAN/01_geometry already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/SWAN/02_bc_dbase already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/SWAN/03_simulation already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/SWAN/04_results already exists
/Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/SWAN/05_processed_results already exists


In [7]:
import generate_config as gc
gc.main(config)

Configuration file generated: /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/SWAN/CONFIG.ini


In [8]:
import create_grid as cg
cg.main(config)

Grids saved to: /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/QGIS/swan_grids.shp


/Users/daniela/Documents/swan/swan_model_builder_tool/create_grid.py:71: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  combined_grids.to_file(output_dir / 'swan_grids.shp')
/Users/daniela/Documents/swan/swan_model_builder_tool/.venv/lib/python3.9/site-packages/pyogrio/raw.py:723: RuntimeWarning: Normalized/laundered field name: 'grid_points' to 'grid_point'
  ogr_write(
/Users/daniela/Documents/swan/swan_model_builder_tool/.venv/lib/python3.9/site-packages/pyogrio/raw.py:723: RuntimeWarning: Value '[(np.float64(-76.5), np.float64(-13.9)), (np.float64(-76.4), np.float64(-13.9)), (np.float64(-76.30000000000001), np.float64(-13.9)), (np.float64(-76.5), np.float64(-13.8)), (np.float64(-76.4), np.float64(-13.8)), (np.float64(-76.30000000000001), np.float64(-13.8)), (np.float64(-76.5), np.float64(-13.700000000000001)), (np.float64(-76.4), np.float64(-13.700000000000001)), (np.float64(-76.30000000000001), np.float64(-13.700000000000001))

In [9]:
import plot_grids as pg
pg.main(config)



Figure saved to: /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/QGIS/swan_grids.png


### TODO agregar las celdas de la bajada de datos

In [31]:
import request_bathy_data as rbd
rbd.main(config)

{'longitude>=': 283.5, 'longitude<=': 283.7, 'latitude>=': -13.9, 'latitude<=': -13.7}


AttributeError: 'NoneType' object has no attribute 'update'

In [10]:
import subset_data_waverys as sdw
sdw.main(config)


Variable time found
Saving subsetted wave data to /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/DATA/WAVE/wave_data_hourly_24-12-2024_03-01-2025_-76.5_-76.3_-13.9_-13.7.nc
Variable time found
Saving subsetted wind data to /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/DATA/WIND/wind_data_hourly_24-12-2024_03-01-2025_-76.5_-76.3_-13.9_-13.7.nc


/Users/daniela/Documents/swan/swan_model_builder_tool/subset_data_waverys.py:104: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.
  if any(dim == 0 for dim in ds_wind_subset.dims.values()):


In [23]:
import build_and_run as br
br.main(config)

Checking required files:
Wind: /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/DATA/WIND/wind_data_hourly_24-12-2024_03-01-2025_-76.5_-76.3_-13.9_-13.7.nc
Wave: /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/DATA/WAVE/wave_data_hourly_24-12-2024_03-01-2025_-76.5_-76.3_-13.9_-13.7.nc
Grid: /Users/daniela/Documents/swan/swan_experiments/run_peninsula_paracas/QGIS/swan_grids.shp


## TODO here the swan must run 

In [12]:
from pathlib import Path

# Asegúrate de que 'config' ya está definido y cargado aquí
base_path = Path(config['base']['path'])
output_dir = config['output']['directory']
sim_dir = base_path / output_dir / 'SWAN/03_simulation'

for grid_key in config['grids']:
    grid = config['grids'][grid_key]
    grid_name = grid['name']
    print(f"Buscando archivos que empiezan con: {grid_name}")
    for f in sorted(sim_dir.glob(f"{grid_name}*")):
        if f.is_file() and not f.name.startswith('.'):
            print(f"  Ejecutando swanrun para: {f.name}")
            !swanrun -input "{f}"

Buscando archivos que empiezan con: REGIONAL_GRID
  Ejecutando swanrun para: REGIONAL_GRID_20241201_20250131.swn
swan.exe is /Users/daniela/Documents/swan/SWAN-41.51-macOS/bin/swan.exe

 SWAN is preparing computation

+SWAN is processing output request    1
+SWAN is processing output request    2
+time 20241201.010000   , step      1; iteration    1; sweep 1
+time 20241201.010000   , step      1; iteration    1; sweep 2
+time 20241201.010000   , step      1; iteration    1; sweep 3
+time 20241201.010000   , step      1; iteration    1; sweep 4
+time 20241201.010000   , step      1; iteration    2; sweep 1
+time 20241201.010000   , step      1; iteration    2; sweep 2
+time 20241201.010000   , step      1; iteration    2; sweep 3
+time 20241201.010000   , step      1; iteration    2; sweep 4
+time 20241201.010000   , step      1; iteration    3; sweep 1
+time 20241201.010000   , step      1; iteration    3; sweep 2
+time 20241201.010000   , step      1; iteration    3; sweep 3
+time 202

In [14]:
import process_results as pr
pr.main(config)

[DEBUG] Buscando archivos NetCDF en: /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results
[DEBUG] Archivos encontrados: []
Converting /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/04_results/REGIONAL_GRID_20241201_20250131.mat to /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results/files/REGIONAL_GRID_20241201_20250131.nc (rotated: True)

Checking file: /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results/files/REGIONAL_GRID_20241201_20250131.nc

Dimensions:
  Yp: 37
  Xp: 31
  time: 1465

Variables:
  Xp:
    shape: (37, 31)
    dtype: float32
    units: m
  Yp:
    shape: (37, 31)
    dtype: float32
    units: m
  time:
    shape: (1465,)
    dtype: datetime64[ns]
  Hsig:
    shape: (1465, 37, 31)
    dtype: float32
    units: m
  TPsmoo:
    shape: (1465, 37, 31)
    d

In [15]:
import process_results as pr
pr.main(config)

[DEBUG] Buscando archivos NetCDF en: /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results/files
[DEBUG] Archivos encontrados: [PosixPath('/Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results/files/TRANSITION_GRID_20241201_20250131.nc'), PosixPath('/Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results/files/REGIONAL_GRID_20241201_20250131.nc')]
Converting /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/04_results/REGIONAL_GRID_20241201_20250131.mat to /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results/files/REGIONAL_GRID_20241201_20250131.nc (rotated: True)

Checking file: /Users/daniela/Documents/swan/swan_experiments/run_storm_event_peru_waverys_dec_2024/SWAN/05_processed_results/files/REGIONAL_GRID_20241201_202501